# PV Rooftops - Aspects
Note: Please make sure your OEDI data lake is deployed.

In this example, the deployed database is named `oedi_database_test`, the table populated is `nrel_pv_rooftops_aspects`.

## 1. Aspects Metadata
The metadata of Aspects table includes 'Columns', 'Partition Keys' and 'Partition Values'. `OEDIGlue` class provides utility methods to retrieve the metadata from a given table.

In [1]:
from oedi.AWS.glue import OEDIGlue

In [2]:
database_name = "oedi_database_test"
table_name = "nrel_pv_rooftops_aspects"

In [3]:
glue = OEDIGlue()

In [4]:
# Table Column Definition
glue.get_table_columns(database_name, table_name)

Name    Type
0                gid  bigint
1               city  string
2              state  string
3               year  bigint
4           bldg_fid  bigint
5             aspect  bigint
6     the_geom_96703  string
7      the_geom_4326  string
8          region_id  bigint
9  __index_level_0__  bigint

In [5]:
# Table Parition Keys
glue.get_partition_keys(database_name, table_name)

Name    Type
0  partition_0  string

In [6]:
# Table Partition Values
glue.get_partition_values(database_name, table_name)

['albuquerque_nm_12',
 'huntsville_al_09',
 'trenton_nj_08',
 'washington_dc_09',
 'norfolk_va_07',
 'providence_ri_04',
 'corpuschristi_tx_12',
 'grandrapids_mi_13',
 'sanbernardinoriverside_ca_12',
 'springfield_il_09',
 'charlotte_nc_06',
 'olympia_wa_10',
 'stlouis_mo_13',
 'charleston_wv_09',
 'newhaven_ct_07',
 'manhattan_ny_07',
 'tampa_fl_13',
 'harrisburg_pa_09',
 'atlanta_ga_13',
 'desmoines_ia_10',
 'washington_dc_12',
 'jackson_ms_07',
 'chicago_il_12',
 'jeffersoncity_mo_08',
 'columbus_ga_09',
 'rochester_ny_14',
 'neworleans_la_08',
 'coloradosprings_co_06',
 'detroit_mi_12',
 'fortwayne_in_08',
 'laguardiajfk_ny_07',
 'albuquerque_nm_06',
 'austin_tx_12',
 'pittsburgh_pa_04',
 'sanfrancisco_ca_13',
 'fresno_ca_06',
 'fresno_ca_13',
 'sandiego_ca_08',
 'jacksonville_fl_10',
 'shreveport_la_08',
 'mobile_al_10',
 'lincoln_ne_08',
 'sanantonio_tx_13',
 'chicago_il_08',
 'kansascity_mo_12',
 'louisville_ky_06',
 'richmond_va_13',
 'missionviejo_ca_13',
 'newhaven_ct_13',
 '

## 2. Run Query
Based on the metadata retrieved above, we can query data by using method in `OEDIAthena` class. In the example below, we select records from partition `topeka_ks_08`.

In [7]:
from pyproj import CRS
from oedi.AWS.athena import OEDIAthena

In [8]:
athena = OEDIAthena(staging_location="s3://nrel-tests", region_name="us-west-2")

In [9]:
query_string = f"""
    SELECT gid, bldg_fid, aspect, the_geom_4326
    FROM {database_name}.{table_name}
    WHERE partition_0='topeka_ks_08'
"""
gdf = athena.run_query(query_string, geometry="the_geom_4326")

In [10]:
gdf.crs = CRS("EPSG:4326")

In [11]:
gdf

gid  bldg_fid  aspect  \
0          496     70560       4   
1          998     70506       3   
2         3949     70217       3   
3         5757     70064       4   
4        20158     68639       4   
...        ...       ...     ...   
853864  853864         1       3   
853865  853865         3       5   
853866  853866         3       4   
853867  853867         1       7   
853868  853869         1       5   

                                            the_geom_4326  
0       MULTIPOLYGON (((-95.78945 39.17040, -95.78945 ...  
1       MULTIPOLYGON (((-95.57186 39.17412, -95.57185 ...  
2       MULTIPOLYGON (((-95.56859 39.16762, -95.56860 ...  
3       MULTIPOLYGON (((-95.72628 39.15991, -95.72628 ...  
4       MULTIPOLYGON (((-95.78229 39.14319, -95.78230 ...  
...                                                   ...  
853864  MULTIPOLYGON (((-95.63141 38.91831, -95.63141 ...  
853865  MULTIPOLYGON (((-95.74384 38.91571, -95.74386 ...  
853866  MULTIPOLYGON (((-95.74384 38.91571, -95.74384 ...  
853867  MULTIPOLYGON (((-95.63152 38.91830, -95.63155 ...  
853868  MULTIPOLYGON (((-95.63151 38.91831, -95.63150 ...  

[853869 rows x 4 columns]

In [12]:
# Check geometry
geom = gdf.iloc[1]["the_geom_4326"]
geom.bounds

(-95.5718572081215, 39.1741102680828, -95.5718453147948, 39.17411952549)

## 3. Aspect Visualization

To visualize the aspect of PV rooftops on map, and see if any trends on its geographic distribution.

In [13]:
import folium
import plotly.graph_objs as go

In [14]:
# Aggregation for counting aspects
agg = gdf.groupby("aspect", as_index=False)["gid"].count()
agg.rename(columns={"gid": "count"}, inplace=True)

# Histogram
aspects = [0, 1, 2, 3, 4, 5, 6, 7, 8]
colors = {
    0: "#ff0000", 
    1: "#ffbf00", 
    2: "#ffff00",
    3: "#00ff00",
    4: "#00ffff",
    5: "#00bfff",
    6: "#0000ff",
    7: "#8000ff",
    8: "#ff00ff"
}
bars = []
for aspect in aspects:
    bar = go.Bar(
        x=[aspect], 
        y=agg[agg["aspect"]==aspect]["count"].values, 
        name=aspect, 
        marker={"color": colors[aspect]}
    )
    bars.append(bar)
fig = go.FigureWidget(data=bars)
fig.layout.title = "Aspect Histogram"
fig

FigureWidget({
    'data': [{'marker': {'color': '#ff0000'},
              'name': '0',
              'type': …

In [15]:
# Sample datasets, otherwise datasets is too large to show.
samples = gdf.sample(n=10000)

In [18]:
imap = folium.Map(location=[39.0473, -95.6752], zoom_start=11, tiles="Stamen Toner")

# Style function
def style_function(feature):
    aspect = feature["properties"]["aspect"]
    return {
        "fillOpacity": 0.75,
        "fillColor": colors[aspect],
        "wight": 0.1,
        "color": colors[aspect]
    }

# GeoJSON
folium.GeoJson(
    name="PV Rooftops",
    data=samples.to_json(),
    style_function=style_function
).add_to(imap)

imap